**IMPORT ALL LIBRARIES**

In [1]:
import pandas as pd
import numpy as np
import contractions
import re

from sentence_transformers import SentenceTransformer
import torch

from umap import UMAP
from hdbscan import HDBSCAN
from sklearn.feature_extraction.text import CountVectorizer

from bertopic import BERTopic

import pickle
import joblib

from gensim.models.coherencemodel import CoherenceModel
from gensim.corpora.dictionary import Dictionary
from sklearn.metrics.pairwise import cosine_similarity

c:\Users\justy\.conda\envs\fyp_dashboard\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


# **LOAD DATASET AND PREPROCESS**

In [2]:
df = pd.read_csv("medical_data.csv")
df

C:\Users\justy\AppData\Local\Temp\ipykernel_27412\3820628763.py:1: DtypeWarning: Columns (43) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv("medical_data.csv")


user_id            username           time  rating  \
0       1.144028e+20          Sajida Dar  1583977664092     5.0   
1       1.027817e+20       Tamara Walker  1604380776309     2.0   
2       1.147746e+20     Christina Veres  1560489213707     4.0   
3       1.108501e+20        Keegan Leahy  1581384638564     1.0   
4       1.106635e+20          Kyle Ebert  1592438884887     2.0   
...              ...                 ...            ...     ...   
316339  1.020788e+20        Kevin Portee  1577891990033     5.0   
316340  1.143790e+20          James Rose  1522868195876     5.0   
316341  1.015381e+20        Maxwell Rosa  1540950220650     5.0   
316342  1.028744e+20      Yolonda Taylor  1536770366671     1.0   
316343  1.128972e+20  Sebastian Domenico  1534967062472     5.0   

                                            original_text  \
0       Great people,great staff and great facility to...   
1       Security guard asked me to put a mask on my 13...   
2       One of the better Cub foods that I have shoppe...   
3       Front of house has amazing staff.. Owner howev...   
4       Came in early\nNo one was there except one per...   
...                                                   ...   
316339            I feel like a new person on every visit   
316340  The aqua therapy I have been receiving there h...   
316341  Had baby #1 last year in June.  Staff was amaz...   
316342  I gave the staff my authorization number for m...   
316343  Dr. Brito and his staff are great! I'll defini...   

                                          translated_text  \
0       Great people,great staff and great facility to...   
1       Security guard asked me to put a mask on my 13...   
2       One of the better Cub foods that I have shoppe...   
3       Front of house has amazing staff.. Owner howev...   
4       Came in early\nNo one was there except one per...   
...                                                   ...   
316339            I feel like a new person on every visit   
316340  The aqua therapy I have been receiving there h...   
316341  Had baby #1 last year in June.  Staff was amaz...   
316342  I gave the staff my authorization number for m...   
316343  Dr. Brito and his staff are great! I'll defini...   

                                      final_with_stopword  \
0       great people great staff and great facility to...   
1       security guard ask me to put a mask on my 13 m...   
2       one of the good cub food that i have shop at e...   
3       front of house have amazing staff owner howeve...   
4       come in early no one be there except one perso...   
...                                                   ...   
316339            i feel like a new person on every visit   
316340  the aqua therapy i have be receive there have ...   
316341  have baby 1 last year in june staff be amaze s...   
316342  i give the staff my authorization number for m...   
316343  dr. brito and his staff be great i will defini...   

                                        final_no_stopword  ori_wc  final_wc  \
0       great people great staff great facility go thu...       9        10   
1       security guard ask put mask 13 month old baby ...      65        68   
2       one good cub food shop everything need right e...      39        39   
3       front house amazing staff owner however lot gr...      51        51   
4       come early no one except one person need simpl...      60        62   
...                                                   ...     ...       ...   
316339                   feel like new person every visit       9         9   
316340                       aqua therapy receive helpful      12        12   
316341  baby 1 last year june staff amaze shoutout mid...      30        30   
316342  give staff authorization number botox injectio...     116       119   
316343  dr. brito staff great definitely trust dental ...      17        18   

        ...  category_12 category_13  category_14  category_

**PREPROCES**

In [3]:
#EXPAND CONTRACTIONS
def expand_cont(text):
    if isinstance(text, str) and text.strip():
        try:
            return contractions.fix(text)
        except IndexError:
            return text
    else:
        return ""

df['cont_expanded'] = df['translated_text'].apply(expand_cont)
df

#CLEAN TEXT
def preprocess_text(text):
    text = text.lower()
    text = re.sub(r"http\S+", "", text)            # Remove URLs
    text = re.sub(r"[^a-z\s]", "", text)           # Remove punctuation/numbers
    text = re.sub(r"\s+", " ", text).strip()       # Normalize whitespace
    return text

#apply preprocessing from the expanded contractions
df['clean_text'] = df['cont_expanded'].apply(preprocess_text)

#CALCULATE WORD COUNT
df['wc'] = df['clean_text'].str.split().str.len()
df

#DROP DUPLICATES
df = df.drop_duplicates(subset='clean_text').reset_index(drop=True)
df

#DROP LOW VALUE TEXT
df = df[df['wc'] >= 5 ].reset_index(drop=True)

In [30]:
df

user_id            username           time  rating  \
0       1.144028e+20          Sajida Dar  1583977664092     5.0   
1       1.027817e+20       Tamara Walker  1604380776309     2.0   
2       1.147746e+20     Christina Veres  1560489213707     4.0   
3       1.108501e+20        Keegan Leahy  1581384638564     1.0   
4       1.106635e+20          Kyle Ebert  1592438884887     2.0   
...              ...                 ...            ...     ...   
305846  1.020788e+20        Kevin Portee  1577891990033     5.0   
305847  1.143790e+20          James Rose  1522868195876     5.0   
305848  1.015381e+20        Maxwell Rosa  1540950220650     5.0   
305849  1.028744e+20      Yolonda Taylor  1536770366671     1.0   
305850  1.128972e+20  Sebastian Domenico  1534967062472     5.0   

                                            original_text  \
0       Great people,great staff and great facility to...   
1       Security guard asked me to put a mask on my 13...   
2       One of the better Cub foods that I have shoppe...   
3       Front of house has amazing staff.. Owner howev...   
4       Came in early\nNo one was there except one per...   
...                                                   ...   
305846            I feel like a new person on every visit   
305847  The aqua therapy I have been receiving there h...   
305848  Had baby #1 last year in June.  Staff was amaz...   
305849  I gave the staff my authorization number for m...   
305850  Dr. Brito and his staff are great! I'll defini...   

                                          translated_text  \
0       Great people,great staff and great facility to...   
1       Security guard asked me to put a mask on my 13...   
2       One of the better Cub foods that I have shoppe...   
3       Front of house has amazing staff.. Owner howev...   
4       Came in early\nNo one was there except one per...   
...                                                   ...   
305846            I feel like a new person on every visit   
305847  The aqua therapy I have been receiving there h...   
305848  Had baby #1 last year in June.  Staff was amaz...   
305849  I gave the staff my authorization number for m...   
305850  Dr. Brito and his staff are great! I'll defini...   

                                      final_with_stopword  \
0       great people great staff and great facility to...   
1       security guard ask me to put a mask on my 13 m...   
2       one of the good cub food that i have shop at e...   
3       front of house have amazing staff owner howeve...   
4       come in early no one be there except one perso...   
...                                                   ...   
305846            i feel like a new person on every visit   
305847  the aqua therapy i have be receive there have ...   
305848  have baby 1 last year in june staff be amaze s...   
305849  i give the staff my authorization number for m...   
305850  dr. brito and his staff be great i will defini...   

                                        final_no_stopword  ori_wc  final_wc  \
0       great people great staff great facility go thu...       9        10   
1       security guard ask put mask 13 month old baby ...      65        68   
2       one good cub food shop everything need right e...      39        39   
3       front house amazing staff owner however lot gr...      51        51   
4       come early no one except one person need simpl...      60        62   
...                                                   ...     ...       ...   
305846                   feel like new person every visit       9         9   
305847                       aqua therapy receive helpful      12        12   
305848  baby 1 last year june staff amaze shoutout mid...      30        30   
305849  give staff authorization number botox injectio...     116       119   
305850  dr. brito staff great definitely trust dental ...      17        18   

        ...  category_16 category_17  category_18  category_

# **LOAD SENTENCE EMBEDDING**

In [4]:
embeddings = np.load("E:/JUSTYN/JUSTYN/BERTOPIC/embeddings.npy")
texts = df['clean_text'].tolist()

In [5]:

np.save("positive_embeddings.npy", embeddings)
embeddings

array([[ 0.04224291, -0.00934046,  0.0281748 , ..., -0.01225406,
        -0.02216125, -0.013539  ],
       [ 0.00086574,  0.12689483, -0.01475409, ..., -0.04474968,
         0.0565543 ,  0.05384716],
       [ 0.04120927, -0.03191343, -0.02362255, ..., -0.02323264,
        -0.02680399, -0.00689324],
       ...,
       [-0.10180993, -0.09129896,  0.04284954, ..., -0.0484487 ,
        -0.01394621,  0.06315085],
       [-0.0371679 ,  0.010715  ,  0.04975103, ..., -0.04702248,
        -0.00412026, -0.00575238],
       [-0.06922076, -0.06632493,  0.02183732, ..., -0.07766668,
         0.01874336,  0.04496736]], dtype=float32)

# **DEFINE UMAP, HDBSCAN, VECTORIZER**

In [6]:
umap_model = UMAP(
    n_neighbors=20,
    n_components=5,
    min_dist=0.0,
    metric="cosine"
)

hdbscan_model = HDBSCAN(
    min_cluster_size=30,
    metric="euclidean",
    cluster_selection_method="eom",
    prediction_data=True  # Required for topic probabilities
)

vectorizer_model = CountVectorizer(ngram_range=(1, 2), stop_words="english")

In [7]:
embeddings

array([[ 0.04224291, -0.00934046,  0.0281748 , ..., -0.01225406,
        -0.02216125, -0.013539  ],
       [ 0.00086574,  0.12689483, -0.01475409, ..., -0.04474968,
         0.0565543 ,  0.05384716],
       [ 0.04120927, -0.03191343, -0.02362255, ..., -0.02323264,
        -0.02680399, -0.00689324],
       ...,
       [-0.10180993, -0.09129896,  0.04284954, ..., -0.0484487 ,
        -0.01394621,  0.06315085],
       [-0.0371679 ,  0.010715  ,  0.04975103, ..., -0.04702248,
        -0.00412026, -0.00575238],
       [-0.06922076, -0.06632493,  0.02183732, ..., -0.07766668,
         0.01874336,  0.04496736]], dtype=float32)

# **INITIALIZE AND FIT BERTOPIC**

In [8]:
# Reuse same embedding model or leave None since you have embeddings already
topic_model = BERTopic(
    umap_model=umap_model,
    hdbscan_model=hdbscan_model,
    vectorizer_model=vectorizer_model,
    calculate_probabilities=True,
    verbose=True
)

# Use the same texts and loaded embeddings
topics, probs = topic_model.fit_transform(texts, embeddings)


2025-07-17 14:32:41,974 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2025-07-17 14:36:21,758 - BERTopic - Dimensionality - Completed ✓
2025-07-17 14:36:21,766 - BERTopic - Cluster - Start clustering the reduced embeddings
2025-07-17 15:33:52,552 - BERTopic - Cluster - Completed ✓
2025-07-17 15:33:52,652 - BERTopic - Representation - Fine-tuning topics using representation models.
2025-07-17 15:34:35,199 - BERTopic - Representation - Completed ✓


# **SAVE EVERYTHING**

**DATASET + CLEANING + ASSIGNED TOPICS**

In [9]:
df["topic"] = topics
df.to_csv("data_with_topic.csv", index=False)
df


user_id            username           time  rating  \
0       1.144028e+20          Sajida Dar  1583977664092     5.0   
1       1.027817e+20       Tamara Walker  1604380776309     2.0   
2       1.147746e+20     Christina Veres  1560489213707     4.0   
3       1.108501e+20        Keegan Leahy  1581384638564     1.0   
4       1.106635e+20          Kyle Ebert  1592438884887     2.0   
...              ...                 ...            ...     ...   
305846  1.020788e+20        Kevin Portee  1577891990033     5.0   
305847  1.143790e+20          James Rose  1522868195876     5.0   
305848  1.015381e+20        Maxwell Rosa  1540950220650     5.0   
305849  1.028744e+20      Yolonda Taylor  1536770366671     1.0   
305850  1.128972e+20  Sebastian Domenico  1534967062472     5.0   

                                            original_text  \
0       Great people,great staff and great facility to...   
1       Security guard asked me to put a mask on my 13...   
2       One of the better Cub foods that I have shoppe...   
3       Front of house has amazing staff.. Owner howev...   
4       Came in early\nNo one was there except one per...   
...                                                   ...   
305846            I feel like a new person on every visit   
305847  The aqua therapy I have been receiving there h...   
305848  Had baby #1 last year in June.  Staff was amaz...   
305849  I gave the staff my authorization number for m...   
305850  Dr. Brito and his staff are great! I'll defini...   

                                          translated_text  \
0       Great people,great staff and great facility to...   
1       Security guard asked me to put a mask on my 13...   
2       One of the better Cub foods that I have shoppe...   
3       Front of house has amazing staff.. Owner howev...   
4       Came in early\nNo one was there except one per...   
...                                                   ...   
305846            I feel like a new person on every visit   
305847  The aqua therapy I have been receiving there h...   
305848  Had baby #1 last year in June.  Staff was amaz...   
305849  I gave the staff my authorization number for m...   
305850  Dr. Brito and his staff are great! I'll defini...   

                                      final_with_stopword  \
0       great people great staff and great facility to...   
1       security guard ask me to put a mask on my 13 m...   
2       one of the good cub food that i have shop at e...   
3       front of house have amazing staff owner howeve...   
4       come in early no one be there except one perso...   
...                                                   ...   
305846            i feel like a new person on every visit   
305847  the aqua therapy i have be receive there have ...   
305848  have baby 1 last year in june staff be amaze s...   
305849  i give the staff my authorization number for m...   
305850  dr. brito and his staff be great i will defini...   

                                        final_no_stopword  ori_wc  final_wc  \
0       great people great staff great facility go thu...       9        10   
1       security guard ask put mask 13 month old baby ...      65        68   
2       one good cub food shop everything need right e...      39        39   
3       front house amazing staff owner however lot gr...      51        51   
4       come early no one except one person need simpl...      60        62   
...                                                   ...     ...       ...   
305846                   feel like new person every visit       9         9   
305847                       aqua therapy receive helpful      12        12   
305848  baby 1 last year june staff amaze shoutout mid...      30        30   
305849  give staff authorization number botox injectio...     116       119   
305850  dr. brito staff great definitely trust dental ...      17        18   

        ...  category_16 category_17  category_18  category_

**TOPIC INFO**

In [10]:
topic_info = topic_model.get_topic_info()
topic_info.to_csv("topic_info.csv", index=False)
topic_info

Topic   Count                                               Name  \
0       -1  142616                          -1_doctor_time_staff_care   
1        0   54006                       0_dentist_dental_teeth_tooth   
2        1    6385                       1_billing_insurance_pay_paid   
3        2    3393                    2_covid_covid test_test_testing   
4        3    3231             3_therapy_physical therapy_physical_pt   
..     ...     ...                                                ...   
342    341      30        341_delivery_deliver_shipping_delivery need   
343    342      30  342_prices need_decent price_need decent_price...   
344    343      30                         343_bugs_bed bugs_bed_ants   
345    344      30                    344_vape_vaping_vape shop_juice   
346    345      30        345_lunch_good lunch_lunch good_place lunch   

                                        Representation  \
0    [doctor, time, staff, care, dr, did, just, app...   
1    [dentist, dental, teeth, tooth, cleaning, offi...   
2    [billing, insurance, pay, paid, collections, p...   
3    [covid, covid test, test, testing, covid testi...   
4    [therapy, physical therapy, physical, pt, shou...   
..                                                 ...   
342  [delivery, deliver, shipping, delivery need, g...   
343  [prices need, decent price, need decent, price...   
344  [bugs, bed bugs, bed, ants, roaches, roach, cr...   
345  [vape, vaping, vape shop, juice, vape bar, vap...   
346  [lunch, good lunch, lunch good, place lunch, p...   

                                   Representative_Docs  
0    [this review is written in regards to my secon...  
1    [i visited the easley office of aspen dental f...  
2    [this is not our usual medical clinic my daugh...  
3    [i do not drive how i get covid test, do not g...  
4    [the staff is so friendly and welcoming i love...  
..                                                 ...  
342  [across the board first time using delivery an...  
343  [usually have what i need for a decent price, ...  
344  [bed bugs are just what the doctor ordered, be...  
345  [best vape store hands down staff is very know...  
346  [great place to get lunch, had lunch it was go...  

[347 rows x 5 columns]

**TOPIC + KEYWORDS + C-TF-IDF SCORES EACH KEYWORD**

In [11]:
topic_info = topic_model.get_topic_info()
topic_ids = topic_info['Topic'].tolist()
#topic keywords + c-td-idf scores for each topic
topic_keywords = []

for topic_id in topic_ids:
    keywords_scores = topic_model.get_topic(topic_id)
    for word, score in keywords_scores:
        topic_keywords.append({
            "Topic": topic_id,
            "Keyword": word,
            "c-TF-IDF": score
        })

topic_keywords

#convert to df
df_keywords = pd.DataFrame(topic_keywords)
df_keywords.to_csv("topic_ctfidf.csv", index=False)
df_keywords


Topic        Keyword  c-TF-IDF
0        -1         doctor  0.002670
1        -1           time  0.002438
2        -1          staff  0.002348
3        -1           care  0.002337
4        -1             dr  0.002229
...     ...            ...       ...
3465    345   lunch dinner  0.044924
3466    345         dinner  0.040809
3467    345     lunch shop  0.040746
3468    345    lunch lunch  0.037828
3469    345  lunch special  0.037179

[3470 rows x 3 columns]

**TOKENIZED TEXT FOR NPMI, DIVERSITY, EMBEDDING COHERENCE**

In [12]:
import pickle

texts_tokenized = [doc.split() for doc in df['clean_text']]
with open("tokenized_positive_text.pkl", "wb") as f:
    pickle.dump(texts_tokenized, f)

texts_tokenized

[['great', 'peoplegreat', 'staff', 'and', 'great', 'facility', 'to', 'go'],
 ['security',
  'guard',
  'asked',
  'me',
  'to',
  'put',
  'a',
  'mask',
  'on',
  'my',
  'month',
  'old',
  'baby',
  'when',
  'i',
  'said',
  'he',
  'is',
  'too',
  'little',
  'he',
  'is',
  'under',
  'two',
  'he',
  'raised',
  'his',
  'eyebrows',
  'and',
  'asked',
  'again',
  'for',
  'me',
  'to',
  'mask',
  'my',
  'baby',
  'please',
  'educate',
  'those',
  'enforcing',
  'policies',
  'so',
  'i',
  'do',
  'not',
  'have',
  'to',
  'defend',
  'a',
  'cdc',
  'policy',
  'which',
  'is',
  'cloth',
  'face',
  'coverings',
  'should',
  'not',
  'be',
  'placed',
  'on',
  'young',
  'children',
  'under',
  'age'],
 ['one',
  'of',
  'the',
  'better',
  'cub',
  'foods',
  'that',
  'i',
  'have',
  'shopped',
  'at',
  'everything',
  'you',
  'need',
  'is',
  'right',
  'there',
  'they',
  'even',
  'have',
  'a',
  'place',
  'to',
  'sit',
  'and',
  'relax',
  'while',
 

**MODEL**

In [13]:
# Save the model to a directory (not a single file)
topic_model.save(
    "model_safetensors_positive",
    serialization="safetensors",  # or "pytorch"
    save_ctfidf=True,
    save_embedding_model="sentence-transformers/all-MiniLM-L6-v2"
)


In [14]:
# Save the model to a directory (not a single file)
topic_model.save(
    "model_pytorch_positive",
    serialization="pytorch",  # or "pytorch"
    save_ctfidf=True,
    save_embedding_model="sentence-transformers/all-MiniLM-L6-v2"
)


# **INTERPRETATION**

**CHECK ONE TOPIC**

In [15]:
#topic X
topic_model.get_topic(103)

[('stitches', 0.055308712268208715),
 ('wound', 0.028235615926763512),
 ('finger', 0.02402035854140455),
 ('cut', 0.01840727944360265),
 ('needed stitches', 0.01046869628678356),
 ('stitch', 0.00899748451132552),
 ('cut finger', 0.008725137258461631),
 ('bleeding', 0.008157036285817465),
 ('stitched', 0.007618980297177249),
 ('glue', 0.007527651545079018)]

In [16]:
#print reviews with topic x
topic_x_reviews = df[df["topic"] == 103]
topic_x_reviews

user_id           username           time  rating  \
286     1.056289e+20        Erica Smith  1563841217989     3.0   
493     1.044740e+20       Anthony Urgo  1543439777737     1.0   
514     1.120096e+20  Steve Kirkpatrick  1577074050203     5.0   
748     1.140708e+20     Chatkan Bunnag  1603225998609     5.0   
1267    1.126040e+20    Zach Carrington  1569623707100     1.0   
...              ...                ...            ...     ...   
295873  1.043312e+20       patrick cote  1593182250585     1.0   
297182  1.032626e+20     Nicole Russell  1555670003246     3.0   
301666  1.143566e+20     chari britnell  1557979048988     4.0   
302455  1.011486e+20        Kaye Kelley  1616796481456     1.0   
303476  1.042466e+20      Sarah Mannion  1572630945281     5.0   

                                            original_text  \
286     Only real big problem was I came in for a poss...   
493     After having a biopsy done and the stiches rem...   
514     I cut my two fingers on my left hand quite bad...   
748     Quick look at cut and stiches.  Able to get ap...   
1267    Worst experience I’ve ever had with an urgent ...   
...                                                   ...   
295873  cut through half my hand was bleeding through ...   
297182  Definitely a mixed bag. I have received EXCELL...   
301666  Only came once for staple removal & evaluation...   
302455  About late 1997 or early 2000 I went in to Dr ...   
303476  My 7 year old busted his chin open and got 3 s...   

                                          translated_text  \
286     Only real big problem was I came in for a poss...   
493     After having a biopsy done and the stiches rem...   
514     I cut my two fingers on my left hand quite bad...   
748     Quick look at cut and stiches.  Able to get ap...   
1267    Worst experience I’ve ever had with an urgent ...   
...                                                   ...   
295873  cut through half my hand was bleeding through ...   
297182  Definitely a mixed bag. I have received EXCELL...   
301666  Only came once for staple removal & evaluation...   
302455  About late 1997 or early 2000 I went in to Dr ...   
303476  My 7 year old busted his chin open and got 3 s...   

                                      final_with_stopword  \
286     only real big problem be i come in for a possi...   
493     after have a biopsy do and the stiches remove ...   
514     i cut my two finger on my left hand quite badl...   
748     quick look at cut and stiches able to get appo...   
1267    bad experience i have ever have with an urgent...   
...                                                   ...   
295873  cut through half my hand be bleed through a be...   
297182  definitely a mixed bag i have receive excellen...   
301666  only come once for staple removal evaluation b...   
302455  about late 1997 or early 2000 i go in to dr bu...   
303476  my 7 year old bust his chin open and get 3 sti...   

                                        final_no_stopword  ori_wc  final_wc  \
286     real big problem come possible infection pract...      42        43   
493     biopsy stiches remove scar come open week late...     161       163   
514     cut two finger left hand quite badly tin roof ...      75        74   
748     quick look cut stiches able get appointment im...      21        21   
1267    bad experience ever urgent care continuously t...      55        59   
...                                                   ...     ...       ...   
295873  cut half hand bleed beach towel tell get call ...      53        53   
297182  definitely mixed bag receive excellent service...     101       102   
301666  come staple removal evaluation fellow andrew '...      20        20   
302455  late 1997 early 2000 go dr budny come anesthes...     101       104   
303476  7 year old bust chin open get 3 stitch forest ...      45        45   

        ...  category_16 category_17  category_18  category_19 category_

**BAR CHART FOR TOPIC'S TOP KEYWORDS**

In [31]:
fig1 = topic_model.visualize_barchart(top_n_topics=347)
fig1

In [32]:
fig1.write_html("A_BERTOPIC_NEG_barchart.html")

**TOPIC RELATIONSHIP = INTERTOPIC DISTANCE MAP**

In [19]:
fig2 = topic_model.visualize_topics()
fig2

In [20]:
fig2.write_html("A_BERTOPIC_NEG_distancemap.html")

**HIERARCHICAL CLUSTERING DENDOGRAM**

In [21]:
# Get total number of topics 
total_topics = len(topic_model.get_topics())
# Use all topics in hierarchy
fig3 = topic_model.visualize_hierarchy(top_n_topics=total_topics)
fig3.show()
fig3.write_html("A_BERTOPIC_NEG_hierarchy.html")

# **EVALUATION**

### **1. GENSIM - WITHOUT OUTLIERS**

In [22]:
from gensim.corpora.dictionary import Dictionary
from gensim.models.coherencemodel import CoherenceModel

In [23]:
# #prepare input
# texts_tokenized = [doc.split() for doc in df['clean_text']]

# #build dictionary and corpus
# dictionary = Dictionary(texts_tokenized)
# corpus = [dictionary.doc2bow(text) for text in texts_tokenized]

# #extract topic keywords
# #each topic = list of words
# topic_words = []
# for topic_id in topic_model.get_topic_info()['Topic']:
#     if topic_id == -1:
#         continue
#     words_scores = topic_model.get_topic(topic_id)
#     if words_scores:  # skip empty topic
#         topic_words.append([word for word, score in words_scores])
    
# #compute coherence
# coherence_model = CoherenceModel(
#     topics=topic_words,
#     texts=texts_tokenized,
#     dictionary=dictionary,
#     coherence='c_v' 
# )
# coherence_model2 = CoherenceModel(
#     topics=topic_words,
#     texts=texts_tokenized,
#     dictionary=dictionary,
#     coherence='u_mass' 
# )
# coherence_model3 = CoherenceModel(
#     topics=topic_words,
#     texts=texts_tokenized,
#     dictionary=dictionary,
#     coherence='c_uci' 
# )
# coherence_model4 = CoherenceModel(
#     topics=topic_words,
#     texts=texts_tokenized,
#     dictionary=dictionary,
#     coherence='c_npmi'  
# )

# coherence_score = coherence_model.get_coherence()
# coherence_score2 = coherence_model2.get_coherence()
# coherence_score3 = coherence_model3.get_coherence()
# coherence_score4 = coherence_model4.get_coherence()
# print("Coherence Score (c_v):", coherence_score)
# print("Coherence Score (u_mass):", coherence_score2)
# print("Coherence Score (c_uci):", coherence_score3)
# print("Coherence Score (c_npmi):", coherence_score4)


In [24]:
from gensim.models import Phrases
from gensim.models.phrases import Phraser
from gensim.corpora.dictionary import Dictionary
from gensim.models.coherencemodel import CoherenceModel

#tokenize documents
texts_tokenized = [doc.split() for doc in df['clean_text']]

#train bigram model
bigram_model = Phrases(texts_tokenized, min_count=3, threshold=10)
bigram_phraser = Phraser(bigram_model)

#apply bigram model to texts
texts_with_phrases = [bigram_phraser[doc] for doc in texts_tokenized]

#build dictionary and corpus 
dictionary = Dictionary(texts_with_phrases)
corpus = [dictionary.doc2bow(text) for text in texts_with_phrases]

#normalize topic words from bertopic
topic_words = []
for topic_id in topic_model.get_topic_info()['Topic']:
    if topic_id == -1:
        continue
    words_scores = topic_model.get_topic(topic_id)

    topic = []
    for word, _ in words_scores:
        # Replace spaces with underscores to match phrases
        word_token = word.replace(" ", "_")
        if word_token in dictionary.token2id:
            topic.append(word_token)

    if len(topic) >= 2:
        topic_words.append(topic)

print(f"Topics retained for coherence: {len(topic_words)}")

#COMPUTE COHERENCE
coherence_model = CoherenceModel(
    topics=topic_words,
    texts=texts_with_phrases,
    dictionary=dictionary,
    coherence='c_v'
)

coherence_model2 = CoherenceModel(
    topics=topic_words,
    texts=texts_with_phrases,
    dictionary=dictionary,
    corpus=corpus,
    coherence='u_mass'
)

coherence_model3 = CoherenceModel(
    topics=topic_words,
    texts=texts_with_phrases,
    dictionary=dictionary,
    coherence='c_uci'
)

coherence_model4 = CoherenceModel(
    topics=topic_words,
    texts=texts_with_phrases,
    dictionary=dictionary,
    coherence='c_npmi'
)

# Display results
print("Coherence Score (c_v):", coherence_model.get_coherence())
print("Coherence Score (u_mass):", coherence_model2.get_coherence())
print("Coherence Score (c_uci):", coherence_model3.get_coherence())
print("Coherence Score (c_npmi):", coherence_model4.get_coherence())



Topics retained for coherence: 345
Coherence Score (c_v): 0.6367987839843254
Coherence Score (u_mass): -4.605794512760808
Coherence Score (c_uci): 0.3245895965604759
Coherence Score (c_npmi): 0.09611192835624054


In [25]:
topic_words

[['dentist',
  'dental',
  'teeth',
  'tooth',
  'cleaning',
  'office',
  'dentists',
  'work',
  'hygienist',
  'dr'],
 ['billing',
  'insurance',
  'pay',
  'paid',
  'collections',
  'payment',
  'billing_department',
  'charged',
  'company',
  'bills'],
 ['covid',
  'covid_test',
  'test',
  'testing',
  'covid_testing',
  'results',
  'tested',
  'rapid',
  'rapid_covid',
  'hours'],
 ['therapy',
  'physical_therapy',
  'physical',
  'pt',
  'shoulder',
  'exercises',
  'therapist',
  'knee',
  'physical_therapist',
  'therapists'],
 ['chiropractic',
  'chiropractor',
  'chiropractors',
  'adjustments',
  'neck',
  'adjustment',
  'dr',
  'pain'],
 ['foot',
  'feet',
  'ankle',
  'podiatrist',
  'toe',
  'shoes',
  'foot_ankle',
  'ingrown',
  'orthotics',
  'inserts'],
 ['massage',
  'massages',
  'massage_therapist',
  'therapist',
  'relaxing',
  'deep_tissue',
  'couples',
  'tissue',
  'tip',
  'couples_massage'],
 ['professional',
  'friendly',
  'helpful',
  'people',
  '

1. c_v = 0 to 1
higher is better.
2. u_mass = negative values
closer to 0 is better.
3. c_uci = 0 to 1+
higher is better
4. c_npmi = -1 to 1
higher is better  
0 is neutral  
values above 0.1 are decent


**RESULT**  
1. c_v = moderate to good
2. u_mass = LOW. maybe bcs sparse data or poor word occurence
3. c_uci = moderate to good
topics are relatively coherent
4. c_npmi = barely acceptable
but 0.1 is a commonly used threshold in topic modeling

### **2. GENSIM - WITH OUTLIERS**

In [26]:
texts_tokenized

[['great', 'peoplegreat', 'staff', 'and', 'great', 'facility', 'to', 'go'],
 ['security',
  'guard',
  'asked',
  'me',
  'to',
  'put',
  'a',
  'mask',
  'on',
  'my',
  'month',
  'old',
  'baby',
  'when',
  'i',
  'said',
  'he',
  'is',
  'too',
  'little',
  'he',
  'is',
  'under',
  'two',
  'he',
  'raised',
  'his',
  'eyebrows',
  'and',
  'asked',
  'again',
  'for',
  'me',
  'to',
  'mask',
  'my',
  'baby',
  'please',
  'educate',
  'those',
  'enforcing',
  'policies',
  'so',
  'i',
  'do',
  'not',
  'have',
  'to',
  'defend',
  'a',
  'cdc',
  'policy',
  'which',
  'is',
  'cloth',
  'face',
  'coverings',
  'should',
  'not',
  'be',
  'placed',
  'on',
  'young',
  'children',
  'under',
  'age'],
 ['one',
  'of',
  'the',
  'better',
  'cub',
  'foods',
  'that',
  'i',
  'have',
  'shopped',
  'at',
  'everything',
  'you',
  'need',
  'is',
  'right',
  'there',
  'they',
  'even',
  'have',
  'a',
  'place',
  'to',
  'sit',
  'and',
  'relax',
  'while',
 

In [27]:
texts_with_phrases

[['great', 'peoplegreat', 'staff', 'and', 'great', 'facility', 'to', 'go'],
 ['security_guard',
  'asked',
  'me',
  'to',
  'put',
  'a',
  'mask',
  'on',
  'my',
  'month_old',
  'baby',
  'when',
  'i',
  'said',
  'he',
  'is',
  'too',
  'little',
  'he',
  'is',
  'under',
  'two',
  'he',
  'raised',
  'his',
  'eyebrows',
  'and',
  'asked',
  'again',
  'for',
  'me',
  'to',
  'mask',
  'my',
  'baby',
  'please',
  'educate',
  'those',
  'enforcing',
  'policies',
  'so',
  'i',
  'do',
  'not',
  'have',
  'to',
  'defend',
  'a',
  'cdc',
  'policy',
  'which',
  'is',
  'cloth',
  'face_coverings',
  'should',
  'not',
  'be',
  'placed',
  'on',
  'young_children',
  'under',
  'age'],
 ['one',
  'of',
  'the',
  'better',
  'cub_foods',
  'that',
  'i',
  'have',
  'shopped',
  'at',
  'everything',
  'you',
  'need',
  'is',
  'right',
  'there',
  'they',
  'even',
  'have',
  'a',
  'place',
  'to',
  'sit',
  'and',
  'relax',
  'while',
  'you',
  'eat',
  'or',


In [28]:
from gensim.models import Phrases
from gensim.models.phrases import Phraser
from gensim.corpora.dictionary import Dictionary
from gensim.models.coherencemodel import CoherenceModel

#tokenize documents
texts_tokenized = [doc.split() for doc in df['clean_text']]

#train bigram model
bigram_model = Phrases(texts_tokenized, min_count=3, threshold=10)
bigram_phraser = Phraser(bigram_model)

#apply bigram model to texts
texts_with_phrases = [bigram_phraser[doc] for doc in texts_tokenized]

#build dictionary and corpus 
dictionary = Dictionary(texts_with_phrases)
corpus = [dictionary.doc2bow(text) for text in texts_with_phrases]

#normalize topic words from bertopic
topic_words = []
for topic_id in topic_model.get_topic_info()['Topic']:
    words_scores = topic_model.get_topic(topic_id)

    topic = []
    for word, _ in words_scores:
        # Replace spaces with underscores to match phrases
        word_token = word.replace(" ", "_")
        if word_token in dictionary.token2id:
            topic.append(word_token)

    if len(topic) >= 2:
        topic_words.append(topic)

print(f"Topics retained for coherence: {len(topic_words)}")

#COMPUTE COHERENCE
coherence_model = CoherenceModel(
    topics=topic_words,
    texts=texts_with_phrases,
    dictionary=dictionary,
    coherence='c_v'
)

coherence_model2 = CoherenceModel(
    topics=topic_words,
    texts=texts_with_phrases,
    dictionary=dictionary,
    corpus=corpus,
    coherence='u_mass'
)

coherence_model3 = CoherenceModel(
    topics=topic_words,
    texts=texts_with_phrases,
    dictionary=dictionary,
    coherence='c_uci'
)

coherence_model4 = CoherenceModel(
    topics=topic_words,
    texts=texts_with_phrases,
    dictionary=dictionary,
    coherence='c_npmi'
)

# Display results
print("Coherence Score (c_v):", coherence_model.get_coherence())
print("Coherence Score (u_mass):", coherence_model2.get_coherence())
print("Coherence Score (c_uci):", coherence_model3.get_coherence())
print("Coherence Score (c_npmi):", coherence_model4.get_coherence())



Topics retained for coherence: 346
Coherence Score (c_v): 0.6359378851456836
Coherence Score (u_mass): -4.59753172103381
Coherence Score (c_uci): 0.3229996536400134
Coherence Score (c_npmi): 0.09576014602206412


### **3. TOPIC DIVERSITY**

In [29]:
def calculate_topic_diversity(topic_words):
    unique_words = set(word for topic in topic_words for word in topic)
    total_words = sum(len(topic) for topic in topic_words)
    return len(unique_words) / total_words

diversity_score = calculate_topic_diversity(topic_words)
print("Topic Diversity:", diversity_score)


Topic Diversity: 0.6238193018480492


# **HIERARCHICAL TOPIC REDUCTION**